In [ ]:
# ..... build coexp network with pseudobulk exp data ..... #

In [2]:
library(dplyr)

In [3]:
## create coexpression network ## 
build_coexp_network <- function(net, method = "spearman", flag = "rank"){
    
    # Calculate correlation coefficients
    genes = rownames(net)
    net = net[rowSums(net) > 0, ]

#     print(paste0("... ",dim(net)[1]," of ",length(genes), " genes have non-zero expression" ))

    net = cor(t(net), method = method)
    
    # Create network
    temp = net[upper.tri(net, diag = T)]
    if (flag == "abs"){
        temp = abs(temp)
    }
    
#     print("...ranking")
    temp = rank(temp, ties.method = "average")  

#     print("...reconstructing matrix")
    net[upper.tri(net, diag = T)] = temp

    net = t(net)
    net[upper.tri(net, diag = T)] = temp

    net = net / max(net, na.rm = T)
    med = median(net, na.rm = T)

    ind = setdiff(genes, rownames(net))   # which genes are missing?

    temp = matrix(med, length(ind), dim(net)[2])
    rownames(temp) = ind

    net = rbind(net, temp)
    temp = matrix(med, dim(net)[1], length(ind))
    colnames(temp) = ind
    net = cbind(net, temp)

    # reorder to original
    net = net[genes, genes]
    diag(net) = 1

    return(net)
}

In [8]:
currspecies = 'lizard'
currstage = 'stage16'
load(paste0(currstage, '_pseudobulk_expression_matrices.Rdata'))
scbulk1[1:2,]

Immature_Endothelium Fibroblasts Endothelial_Capillaries
LOC132761864 0.81595004           5.492649    3.769192               
LOC132781240 0.03308073           1.257730    0.000000               
             Cardiomyocytes Myeloid_Immune_Cells Endocardial Immature_FB-like
LOC132761864 7.750231       1.627535             1.681224    6.41687         
LOC132781240 2.536928       0.000000             0.000000    0.00000         
             Neuronal_Cells Immature_Cardiomyocytes Lymphoid_Immune_Cells
LOC132761864 0              6.0915735               3.905624             
LOC132781240 0              0.4668186               0.000000             
             Pericytes Immature_Neuralcrest Smooth_Muscle_Cells
LOC132761864 15.38336  15.03986             6.380217           
LOC132781240  0.00000   0.00000             0.000000           
             Endothelial_Venous Endothelial_Arterial Epicardium_FB-like
LOC132761864 1.737849           0                    16.83904          
LOC132781240 0.000000           0                     0.00000

In [9]:
# correlate across all subclasses
options(warn = -1)
cor1 = build_coexp_network(scbulk1, method = 'spearman')
dim(cor1)
cor1[1:3,1:3]

# save
fileo = paste0(currspecies, '_', currstage, '_coexp_net.Rdata')
save(cor1, file = fileo)

[1] 22719 22719

LOC132761864 LOC132781240 LOC132781182
LOC132761864 1.0000000    0.5573218    0.3119206   
LOC132781240 0.5573218    1.0000000    0.9788479   
LOC132781182 0.3119206    0.9788479    1.0000000